# Building RDME geometry from scratch

Tyler Earnest

"Hands-On" Workshop on Cell Scale simulations at Urbana, IL

July 20, 2018

# Objective

Compose a site type lattice using geometric primitives

# Site type lattice

* 3D array of `uint8`
* Site type specifies
    * Possible reactions
    * Diffusion: within site type, and transitions between site types

# Methods available in Lattice Microbes

*pyLM*
* Define simulation volume as abstract geometric primitives
* Once the represention is complete, the model is discretized onto a lattice representation
* Well tested, more geometric primitives
* Poor control over features near the lattice representation
    * Membranes
    * Pores
    * Filiments

# Methods available in Lattice Microbes
*jLM*
* Define simulation volume as binary arrays of the same shape as the lattice
* No explicit discretization
* New implementation, less well tested, fewer geometric primitives available (for now)

# pyLM example: *E. coli* cell


Regions
* Extracellular
* Membrane
    * $3.6\;\mu m$ long by $0.8\;\mu m$ thick.
* Cytoplasm
* Cytoplasmic obstructions
* Nucleoid
    * Half of the radius

# pyLM: *E. coli* cell
![](eco.png)

# Imports

In [ ]:
%matplotlib notebook

In [ ]:
import lm
import pyLM
from pyLM.RDME import RDMESimulation
import pyLM.units as lmunits
import pySTDLM
import pyLM.ipyInterface as ipylm

import numpy as np
import math
import scipy as sp
import scipy.spatial as spspat

import matplotlib.pyplot as plt

# Simulation volume

Define `RDMESimulation`
* Simulation volume size
* Lattice spacing
* Default region: name of site type 0

In [ ]:
sim = RDMESimulation(dimensions=lmunits.micron(1.024,1.024,4.096), 
                     spacing=lmunits.nm(32), 
                     name="E. coli",
                     defaultRegion="extracellular")

In [ ]:
cyt = sim.addRegion("cytoplasm")
mem = sim.addRegion("membrane")
nuc = sim.addRegion("nucleoid")

In [ ]:
cytType = sim.siteTypes['cytoplasm']
memType = sim.siteTypes['membrane']
nucType = sim.siteTypes['nucleoid']

# Define the lengths

In [ ]:
cell_length = 3.6
cell_width = 0.8
membrane_thickness = 0.032
nucleoid_width = cell_width/2

In [ ]:
cylinderLength = cell_length - cell_width

simulation_center = np.array([0.512, 0.512, 2.048])

cap_center1 = simulation_center - [0,0,0.5*cylinderLength]
cap_center2 = simulation_center + [0,0,0.5*cylinderLength]

p1 = lm.point(lmunits.micron(cap_center1[0]),
              lmunits.micron(cap_center1[1]),
              lmunits.micron(cap_center1[2]))

p2 = lm.point(lmunits.micron(cap_center2[0]),
              lmunits.micron(cap_center2[1]),
              lmunits.micron(cap_center2[2]))

# Cell building with pyLM

Regions are defined and stacked together

![](eco2.png)

Start from bottom of stack and work up

# Build cell membrane

In [ ]:
radius = lmunits.micron(0.5*cell_width)

mem_sphere1 = lm.Sphere(p1, radius, memType)
mem_sphere2 = lm.Sphere(p2, radius, memType)
mem_cylinder = lm.Cylinder(p1, p2, radius, memType)

# Build cytoplasm

In [ ]:
radius = lmunits.micron(0.5*cell_width-membrane_thickness)

cyt_sphere1 = lm.Sphere(p1, radius, cytType)
cyt_sphere2 = lm.Sphere(p2, radius, cytType)
cyt_cylinder = lm.Cylinder(p1, p2, radius, cytType)

# Build nucleoid

In [ ]:
radius = lmunits.micron(0.5*nucleoid_width)

nuc_sphere1 = lm.Sphere(p1, radius, nucType)
nuc_sphere2 = lm.Sphere(p2, radius, nucType)
nuc_cylinder = lm.Cylinder(p1, p2, radius, nucType)

# Compose the site type geometry

Order matters!

In [ ]:
sim.lm_builder.addRegion(mem_sphere1)
sim.lm_builder.addRegion(mem_sphere2)
sim.lm_builder.addRegion(mem_cylinder)

sim.lm_builder.addRegion(cyt_sphere1)
sim.lm_builder.addRegion(cyt_sphere2)
sim.lm_builder.addRegion(cyt_cylinder)

sim.lm_builder.addRegion(nuc_sphere1)
sim.lm_builder.addRegion(nuc_sphere2)
sim.lm_builder.addRegion(nuc_cylinder)

In [ ]:
ipylm.visualizeRDMEInitialConditions(sim)

# Membrane looks irregular?

Generating a membrane this way can be problematic.
* It's thicker in some regions
* More subtle problem: connectivity
    * Membrane proteins cannot diffuse to all parts of the membrane

# Connectivity problems

Not really obvious by inspecting the widget output

Check with image labeling

# Binary image labeling

For a binary image with multiple disconnected regions, we can associate with each region a unique number

# Consider the following binary image

In [ ]:
box1 = np.zeros((64,64), dtype=bool)
box1[10:20, 10:20] = True
box2 = np.zeros((64,64), dtype=bool)
box2[30:40, 20:40] = True
im = box1|box2
fig, ax = plt.subplots()
ax.imshow(im, cmap='jet', interpolation='nearest')

# Label the image

Using `scipy.ndimage.label` we count labeled regions and get a transformed version of the binary image with each region set to an integer label

In [ ]:
import scipy.ndimage as spnd
labeled, nlabels = spnd.label(im)
print("number of labels", nlabels)
print("background", labeled[0,0])
print("box1 label", labeled[box1][0])
print("box2 label", labeled[box2][0])

In [ ]:
fig, ax = plt.subplots()
ax.imshow(labeled, cmap='jet', interpolation='nearest')

# Connectivity
In LM particles can only hop between *nearest neighbor* sites.

In [ ]:
box1 = np.zeros((64,64), dtype=bool)
box1[10:20, 10:20] = True
box2 = np.zeros((64,64), dtype=bool)
box2[20:30, 20:30] = True
im = box1|box2
labeled, n = spnd.label(im)

fig, ax = plt.subplots(ncols=2)
ax[0].imshow(im, cmap='jet', interpolation='nearest')
ax[1].imshow(labeled, cmap='jet', interpolation='nearest')

These regions are disconnected: a particle in the green region can never enter the red

# Check to see if the membrane is connected

In [ ]:
siteTypeLattice = sim.lattice.getSiteLatticeView()
membrane = siteTypeLattice == sim.siteTypes["membrane"]
labeled, nlabels = spnd.label(membrane)
print("disjoint regions", nlabels)

In [ ]:
fig, ax = plt.subplots()
plt.imshow(labeled[:,16,:].T, cmap='jet')

# How to fix it?

Make a thicker membrane, or reduce the lattice spacing

But what if you want need the membrane thickness to be equal to the lattice spacing

Need to work with the site type lattice directly: jLM!